# Fuzzy Matching with RL - 247 & Rivals

> Leveraging the RL library to determine approximate matching over a range of fields using various string methods methods.  This specifically focuses on 247 & Rivals first.

In [ ]:
import json
import pandas
import time
import os
import recordlinkage
import csv
import core_constants as cc
import functions as fx

#not currently using jellyfish
import jellyfish as jf

### I don't like having all of this here - should push to functions

In [ ]:
outputDir = '..//scrapedData//'
field_agg = "_"

## Load the source file dict
sourceFiles = json.loads(open('..//config//sourceFiles.json', "r").read())

## Load the id config
idConfig = json.loads(open('..//config//idConfig.json', "r").read())

## Load and Merge Source Files Then Create a List of Dicts for each Dataset
> This was originally set up for all of the keys in the sourcefiles.json config.  Since this file is currently only going to serve 247 & Rivals, I've hardcoded the keys to fetch

In [ ]:
dataset_keys = ['sports247', 'rivals']
for dataset in dataset_keys:
    SQL = """SELECT * FROM {}""".format(dataset)
    vars()[dataset] = fx.connDBAndReturnDF(SQL)

In [ ]:
rivals.head()

rawSchool    school  year     playerName           city state    highSchool  \
0  Michigan  michigan  2004     alanbranch    Albuquerque    NM        Cibola   
1  Michigan  michigan  2009       craigroh     Scottsdale    AZ     Chaparral   
2  Maryland  maryland  2003       dremoore      Charlotte    NC  Independence   
3  Maryland  maryland  2016   darrylturner    Hyattsville    MD       DeMatha   
4   Rutgers   rutgers  2005  ryanblaszczyk  Medford Lakes    NJ       Shawnee   

  position  height  weight  stars  nationalRank  positionRank  stateRank  \
0       OL    78.0   315.0      4           NaN          20.0        NaN   
1       DE    77.0   230.0      4         156.0           7.0        4.0   
2       DT    76.0   275.0      2           NaN           NaN        NaN   
3      ATH    69.0   188.0      4           NaN          17.0        7.0   
4       OL    76.0   301.0      2           NaN           NaN        NaN   

     displayName                     ID                        IDYR  
0     alanbranch    alanbranch_michigan    alanbranch_michigan_2004  
1       craigroh      craigroh_michigan      craigroh_michigan_2009  
2       dremoore      dremoore_maryland      dremoore_maryland_2003  
3   darrylturner  darrylturner_maryland  darrylturner_maryland_2016  
4  ryanblaszczyk  ryanblaszczyk_rutgers  ryanblaszczyk_rutgers_2005

## Create New IDs
> This isn't elegant and I'd love to basically preprocess these collections prior to this notebook

NOTE: This has been pushed to the DB write in the earlier dataset related notebook!!!

fx.createNewID(idConfig['sports247'], sports247, field_agg)
fx.createNewID(idConfig['rivals'], rivals, field_agg)

## Create Dataframes
> I might move these to their own pickles so I don't constantly have to recreate these each time

In [ ]:
sports247.set_index('IDYR')
rivals.set_index('IDYR')

rawSchool            school  year  \
IDYR                                                                          
alanbranch_michigan_2004                   Michigan          michigan  2004   
craigroh_michigan_2009                     Michigan          michigan  2009   
dremoore_maryland_2003                     Maryland          maryland  2003   
darrylturner_maryland_2016                 Maryland          maryland  2016   
ryanblaszczyk_rutgers_2005                  Rutgers           rutgers  2005   
...                                             ...               ...   ...   
scottlove_louisianamonroe_2006            UL-Monroe   louisianamonroe  2006   
quanterioheath_arkansasstate_2012    Arkansas State     arkansasstate  2012   
courtlandfuller_troy_2005                      Troy              troy  2005   
rashaadtownes_appalachianstate_2013  Appalachian St  appalachianstate  2013   
navyharris_troy_2020                           Troy              troy  2020   

                                          playerName           city state  \
IDYR                                                                        
alanbranch_michigan_2004                  alanbranch    Albuquerque    NM   
craigroh_michigan_2009                      craigroh     Scottsdale    AZ   
dremoore_maryland_2003                      dremoore      Charlotte    NC   
darrylturner_maryland_2016              darrylturner    Hyattsville    MD   
ryanblaszczyk_rutgers_2005             ryanblaszczyk  Medford Lakes    NJ   
...                                              ...            ...   ...   
scottlove_louisianamonroe_2006             scottlove    West Monroe    LA   
quanterioheath_arkansasstate_2012     quanterioheath          Rison    AR   
courtlandfuller_troy_2005            courtlandfuller       Columbus    GA   
rashaadtownes_appalachianstate_2013    rashaadtownes          Macon    GA   
navyharris_troy_2020                      navyharris     Hutchinson    KS   

                                          highSchool position  height  weight  \
IDYR                                                                            
alanbranch_michigan_2004                      Cibola       OL    78.0   315.0   
craigroh_michigan_2009                     Chaparral       DE    77.0   230.0   
dremoore_maryland_2003                  Independence       DT    76.0   275.0   
darrylturner_maryland_2016                   DeMatha      ATH    69.0   188.0   
ryanblaszczyk_rutgers_2005                   Shawnee       OL    76.0   301.0   
...                                              ...      ...     ...     ...   
scottlove_louisianamonroe_2006           West Monroe        K    72.0   205.0   
quanterioheath_arkansasstate_2012              Rison       LB    75.0   210.0   
courtlandfuller_troy_2005                   Kendrick       WR    72.0   172.0   
rashaadtownes_appalachianstate_2013           Howard       DB    74.0   207.0   
navyharris_troy_2020                 Hutchinson C.C.       LB    73.0   235.0   

                                     stars  nationalRank  positionRank  \
IDYR                                                                     
alanbranch_michigan_2004                 4           NaN          20.0   
craigroh_michigan_2009                   4         156.0           7.0   
dremoore_maryland_2003                   2           NaN           NaN   
darrylturner_maryland_2016               4           NaN          17.0   
ryanblaszczyk_rutgers_2005               2           NaN           NaN   
...                                    ...           ...           ...   
scottlove_louisianamonroe_2006           2           NaN           NaN   
quanterioheath_arkansasstate_2012        3           NaN           NaN   
courtlandfuller_troy_2005                2           NaN           NaN   
rashaadtownes_appalachianstate_2013      2           NaN           NaN   
navyharris_troy_2020                     2           NaN           NaN

## Rename the indexes to something readable and predictable
> Otherwise these become 'index' and 'level_0', etc when you start to merge these.

In [ ]:
sports247.index.name = '247_IDYR'
#sports247['ID'] = df_sports247.index
rivals.index.name = 'rivals_IDYR'
#df_rivals['ID'] = df_rivals.index

## Create Blockers
> I swear this isn't working.  And honestly I guess I'm ok with it not working since I'm doing string operations later on this script.  This usually takes 20+ minutes - so it is doing something...

In [ ]:
indexer = recordlinkage.BlockIndex(on=['school', 'year'])
candidate_links = indexer.index(sports247, rivals)

## Define Features & Generate Comparison Vector Set

> These are all pretty straightforward.  The toughest one to assess is position - since the services don't always categorize players in the same way or have the same abbreviation for a single position.  Since this is often only a 2 or 3 letter string, I decided to do an exact match.

In [ ]:
c = recordlinkage.Compare()

c.exact('IDYR', 'IDYR', label='IDYR')
c.string('playerName', 'playerName', method='damerau_levenshtein', label='playerName')
# don't need this since you are now blocking on it
#c.string('school', 'school', label='college')
c.string('city', 'city', label='city')
c.exact('state', 'state', label='state')
c.string('highSchool', 'highSchool', label='highSchool')
c.exact('position', 'position', label='position')
#c.exact('year', 'year', label='year')

features = c.compute(candidate_links, sports247, rivals)

## Create Sum
> Final value will be between 0 and 1.  Sum represents a %confidence% level during fuzzy matching. Since an exact match on ID dictates a 100% confident match, I've removed that column from the sum.

In [ ]:
features['sum'] = (features['playerName'] + features['city'] + features['state'] + features['highSchool']  + features['position'])/5

In [ ]:
features.head()

IDYR  playerName      city  state  highSchool  position  \
247_IDYR rivals_IDYR                                                            
0        515             0    0.285714  0.000000      0    0.090909         0   
         603             0    0.166667  0.000000      0    0.125000         0   
         2727            0    0.000000  0.166667      0    0.090909         0   
         2849            0    0.083333  0.166667      0    0.090909         0   
         2906            0    0.071429  0.000000      0    0.066667         0   

                           sum  
247_IDYR rivals_IDYR            
0        515          0.075325  
         603          0.058333  
         2727         0.051515  
         2849         0.068182  
         2906         0.027619

## Filter by Threshold

> Agreed upon confidence level for 247 & Rivals is .6943.  

In [ ]:
count = 0
filteredList = []
noMatch = []

features['247_ID'] = features.index.get_level_values(0)
features['rivals'] = features.index.get_level_values(1)

for idx, data in features.groupby(level=0):
    data = data.loc[data['sum'].idxmax()]
    if (data['IDYR'] == 1):
        filteredList.append(data)
    elif (data['IDYR'] != 1 and data['sum'] > .6943):
        filteredList.append(data)
    else:
        noMatch.append(data)

In [ ]:
print(filteredList[0])

IDYR             1.0
playerName       1.0
city             1.0
state            1.0
highSchool       1.0
position         0.0
sum              0.8
247_ID           0.0
rivals        3811.0
Name: (0, 3811), dtype: float64


In [ ]:
dfFinal = pandas.DataFrame()
dfFinal = dfFinal.append(filteredList)

In [ ]:
dfFinal.head()

IDYR  playerName  city  state  highSchool  position     sum  \
(0, 3811)   1.0         1.0   1.0    1.0      1.0000       0.0  0.8000   
(1, 5472)   1.0         1.0   1.0    1.0      0.3125       0.0  0.6625   
(2, 4696)   1.0         1.0   1.0    1.0      0.4375       1.0  0.8875   
(3, 3372)   1.0         1.0   1.0    1.0      1.0000       1.0  1.0000   
(4, 515)    1.0         1.0   1.0    1.0      1.0000       0.0  0.8000   

           247_ID  rivals  
(0, 3811)     0.0  3811.0  
(1, 5472)     1.0  5472.0  
(2, 4696)     2.0  4696.0  
(3, 3372)     3.0  3372.0  
(4, 515)      4.0   515.0

In [ ]:
## There might be something missing here - no idea how rivals_IDYR with the index came to be...
rivals.head()

rawSchool    school  year     playerName           city state  \
rivals_IDYR                                                                 
0            Michigan  michigan  2004     alanbranch    Albuquerque    NM   
1            Michigan  michigan  2009       craigroh     Scottsdale    AZ   
2            Maryland  maryland  2003       dremoore      Charlotte    NC   
3            Maryland  maryland  2016   darrylturner    Hyattsville    MD   
4             Rutgers   rutgers  2005  ryanblaszczyk  Medford Lakes    NJ   

               highSchool position  height  weight  stars  nationalRank  \
rivals_IDYR                                                               
0                  Cibola       OL    78.0   315.0      4           NaN   
1               Chaparral       DE    77.0   230.0      4         156.0   
2            Independence       DT    76.0   275.0      2           NaN   
3                 DeMatha      ATH    69.0   188.0      4           NaN   
4                 Shawnee       OL    76.0   301.0      2           NaN   

             positionRank  stateRank    displayName                     ID  \
rivals_IDYR                                                                  
0                    20.0        NaN     alanbranch    alanbranch_michigan   
1                     7.0        4.0       craigroh      craigroh_michigan   
2                     NaN        NaN       dremoore      dremoore_maryland   
3                    17.0        7.0   darrylturner  darrylturner_maryland   
4                     NaN        NaN  ryanblaszczyk  ryanblaszczyk_rutgers   

                                   IDYR  
rivals_IDYR                              
0              alanbranch_michigan_2004  
1                craigroh_michigan_2009  
2                dremoore_maryland_2003  
3            darrylturner_maryland_2016  
4            ryanblaszczyk_rutgers_2005

In [ ]:
sportDict = sports247.to_dict('records')
rivalsDict = rivals.to_dict('records')
sportDict[0]

{'index': 0,
 '247_IDYR': 0,
 'school': 'nebraska',
 'year': '2012',
 'playerName': 'paulthurston',
 'highSchool': 'Arvada West',
 'city': 'Arvada',
 'state': 'CO',
 'position': 'OT',
 'height': '77.0',
 'weight': '275',
 'compRating': '0.9407',
 'compStars': 4,
 'nationalRank': '152',
 'positionRank': '16',
 'stateRank': '2',
 '247Rating': ' 92  ',
 '247Stars': 4.0,
 '247positionRank': '26',
 '247stateRank': '2',
 'displayName': 'paulthurston',
 'ID': 'paulthurston_nebraska',
 'IDYR': 'paulthurston_nebraska_2012',
 '247nationalRank': None}

In [ ]:
finalSet = []
for record in sportDict:
    
    finalRecord = {}
    for key,value in record.items():
        finalRecord[key] = value
    
    try:
        multiResults = features.loc[features['247_IDYR'] == record['247_IDYR']]
        rivalsID = multiResults['rivals'].values
        
        if (multiResults['ID'].max() == 1):
            finalRecord['confidence'] = 1
        else:
            finalRecord['confidence'] = multiResults['sum'].max()
    
    except Exception as e:
        finalRecord['error'] = 'No feature found with that ID'

    try:
        rivalsResult = (rivals.loc[rivals['ID'] == rivalsID[0]]).to_dict()
        
        for key, value in rivalsResult.items():
            finalRecord['r_' + key] = value[rivalsID[0]]
    
    except Exception as e:
        finalRecord['error'] = 'No rivals match found'
    
    finalSet.append(finalRecord)

In [ ]:
finalSet[0]

{'index': 0,
 '247_IDYR': 0,
 'school': 'nebraska',
 'year': '2012',
 'playerName': 'paulthurston',
 'highSchool': 'Arvada West',
 'city': 'Arvada',
 'state': 'CO',
 'position': 'OT',
 'height': '77.0',
 'weight': '275',
 'compRating': '0.9407',
 'compStars': 4,
 'nationalRank': '152',
 'positionRank': '16',
 'stateRank': '2',
 '247Rating': ' 92  ',
 '247Stars': 4.0,
 '247positionRank': '26',
 '247stateRank': '2',
 'displayName': 'paulthurston',
 'ID': 'paulthurston_nebraska',
 'IDYR': 'paulthurston_nebraska_2012',
 '247nationalRank': None,
 'error': 'No rivals match found'}

In [ ]:
count = 0
for rival in rivalsDict:
    found = 0
    
    for record in finalSet:
        if ('r_ID' in record.keys() and rival['ID'] == record['r_ID']):
            found = 1

    if (found == 0):
        newPlayer = {}
        for key, value in rival.items():
            newPlayer['r_' + key] = value
        newPlayer['school'] = rival['school']
        newPlayer['year'] = rival['year']
        print(newPlayer)
        count = count + 1
        finalSet.append(newPlayer)

print(count)

{'r_rawSchool': 'Michigan', 'r_school': 'michigan', 'r_year': '2004', 'r_playerName': 'alanbranch', 'r_city': 'Albuquerque', 'r_state': 'NM', 'r_highSchool': 'Cibola', 'r_position': 'OL', 'r_height': 78.0, 'r_weight': 315.0, 'r_stars': 4, 'r_nationalRank': nan, 'r_positionRank': 20.0, 'r_stateRank': nan, 'r_displayName': 'alanbranch', 'r_ID': 'alanbranch_michigan', 'r_IDYR': 'alanbranch_michigan_2004', 'school': 'michigan', 'year': '2004'}
{'r_rawSchool': 'Michigan', 'r_school': 'michigan', 'r_year': '2009', 'r_playerName': 'craigroh', 'r_city': 'Scottsdale', 'r_state': 'AZ', 'r_highSchool': 'Chaparral', 'r_position': 'DE', 'r_height': 77.0, 'r_weight': 230.0, 'r_stars': 4, 'r_nationalRank': 156.0, 'r_positionRank': 7.0, 'r_stateRank': 4.0, 'r_displayName': 'craigroh', 'r_ID': 'craigroh_michigan', 'r_IDYR': 'craigroh_michigan_2009', 'school': 'michigan', 'year': '2009'}
{'r_rawSchool': 'Maryland', 'r_school': 'maryland', 'r_year': '2003', 'r_playerName': 'dremoore', 'r_city': 'Charlott

{'r_rawSchool': 'Penn State', 'r_school': 'pennstate', 'r_year': '2019', 'r_playerName': 'brandonsmith', 'r_city': 'Mineral', 'r_state': 'VA', 'r_highSchool': 'Louisa County', 'r_position': 'LB', 'r_height': 75.0, 'r_weight': 225.0, 'r_stars': 4, 'r_nationalRank': 39.0, 'r_positionRank': 3.0, 'r_stateRank': 1.0, 'r_displayName': 'brandonsmith', 'r_ID': 'brandonsmith_pennstate', 'r_IDYR': 'brandonsmith_pennstate_2019', 'school': 'pennstate', 'year': '2019'}
{'r_rawSchool': 'Ohio State', 'r_school': 'ohiostate', 'r_year': '2019', 'r_playerName': 'tommyeichenberg', 'r_city': 'Cleveland', 'r_state': 'OH', 'r_highSchool': 'St. Ignatius', 'r_position': 'LB', 'r_height': 75.0, 'r_weight': 225.0, 'r_stars': 4, 'r_nationalRank': 213.0, 'r_positionRank': 12.0, 'r_stateRank': 6.0, 'r_displayName': 'tommyeichenberg', 'r_ID': 'tommyeichenberg_ohiostate', 'r_IDYR': 'tommyeichenberg_ohiostate_2019', 'school': 'ohiostate', 'year': '2019'}
{'r_rawSchool': 'Michigan', 'r_school': 'michigan', 'r_year': '

{'r_rawSchool': 'Ohio State', 'r_school': 'ohiostate', 'r_year': '2017', 'r_playerName': 'joshmyers', 'r_city': 'Miamisburg', 'r_state': 'OH', 'r_highSchool': 'Miamisburg', 'r_position': 'OL', 'r_height': 77.0, 'r_weight': 280.0, 'r_stars': 4, 'r_nationalRank': 55.0, 'r_positionRank': 2.0, 'r_stateRank': 1.0, 'r_displayName': 'joshmyers', 'r_ID': 'joshmyers_ohiostate', 'r_IDYR': 'joshmyers_ohiostate_2017', 'school': 'ohiostate', 'year': '2017'}
{'r_rawSchool': 'Maryland', 'r_school': 'maryland', 'r_year': '2017', 'r_playerName': 'carloscarriere', 'r_city': 'Alpharetta', 'r_state': 'GA', 'r_highSchool': 'Alpharetta', 'r_position': 'WR', 'r_height': 77.0, 'r_weight': 170.0, 'r_stars': 3, 'r_nationalRank': nan, 'r_positionRank': 95.0, 'r_stateRank': 77.0, 'r_displayName': 'carloscarriere', 'r_ID': 'carloscarriere_maryland', 'r_IDYR': 'carloscarriere_maryland_2017', 'school': 'maryland', 'year': '2017'}
{'r_rawSchool': 'Northwestern', 'r_school': 'northwestern', 'r_year': '2017', 'r_player

{'r_rawSchool': 'Wisconsin', 'r_school': 'wisconsin', 'r_year': '2006', 'r_playerName': 'rickygarner', 'r_city': 'Pasadena', 'r_state': 'CA', 'r_highSchool': 'Muir', 'r_position': 'DE', 'r_height': 77.0, 'r_weight': 225.0, 'r_stars': 2, 'r_nationalRank': nan, 'r_positionRank': nan, 'r_stateRank': nan, 'r_displayName': 'rickygarner', 'r_ID': 'rickygarner_wisconsin', 'r_IDYR': 'rickygarner_wisconsin_2006', 'school': 'wisconsin', 'year': '2006'}
{'r_rawSchool': 'Maryland', 'r_school': 'maryland', 'r_year': '2017', 'r_playerName': 'lawtezrogers', 'r_city': 'Greenbelt', 'r_state': 'MD', 'r_highSchool': 'Eleanor Roosevelt', 'r_position': 'DE', 'r_height': 76.0, 'r_weight': 245.0, 'r_stars': 3, 'r_nationalRank': nan, 'r_positionRank': 25.0, 'r_stateRank': 14.0, 'r_displayName': 'lawtezrogers', 'r_ID': 'lawtezrogers_maryland', 'r_IDYR': 'lawtezrogers_maryland_2017', 'school': 'maryland', 'year': '2017'}
{'r_rawSchool': 'Northwestern', 'r_school': 'northwestern', 'r_year': '2012', 'r_playerName

{'r_rawSchool': 'Nebraska', 'r_school': 'nebraska', 'r_year': '2007', 'r_playerName': 'royhelu', 'r_city': 'Danville', 'r_state': 'CA', 'r_highSchool': 'San Ramon Valley', 'r_position': 'RB', 'r_height': 71.0, 'r_weight': 206.0, 'r_stars': 3, 'r_nationalRank': nan, 'r_positionRank': 55.0, 'r_stateRank': nan, 'r_displayName': 'royhelu', 'r_ID': 'royhelu_nebraska', 'r_IDYR': 'royhelu_nebraska_2007', 'school': 'nebraska', 'year': '2007'}
{'r_rawSchool': 'Northwestern', 'r_school': 'northwestern', 'r_year': '2015', 'r_playerName': 'traewilliams', 'r_city': 'The Plains', 'r_state': 'OH', 'r_highSchool': 'Athens', 'r_position': 'ATH', 'r_height': 71.0, 'r_weight': 189.0, 'r_stars': 3, 'r_nationalRank': nan, 'r_positionRank': nan, 'r_stateRank': 49.0, 'r_displayName': 'traewilliams', 'r_ID': 'traewilliams_northwestern', 'r_IDYR': 'traewilliams_northwestern_2015', 'school': 'northwestern', 'year': '2015'}
{'r_rawSchool': 'Illinois', 'r_school': 'illinois', 'r_year': '2002', 'r_playerName': 'sc

...

{'r_rawSchool': 'Auburn', 'r_school': 'auburn', 'r_year': '2014', 'r_playerName': 'stephenroberts', 'r_city': 'Opelika', 'r_state': 'AL', 'r_highSchool': 'Opelika', 'r_position': 'DB', 'r_height': 73.0, 'r_weight': 179.0, 'r_stars': 4, 'r_nationalRank': 170.0, 'r_positionRank': 13.0, 'r_stateRank': 9.0, 'r_displayName': 'stephenroberts', 'r_ID': 'stephenroberts_auburn', 'r_IDYR': 'stephenroberts_auburn_2014', 'school': 'auburn', 'year': '2014'}
{'r_rawSchool': 'Georgia', 'r_school': 'georgia', 'r_year': '2015', 'r_playerName': 'ricomcgraw', 'r_city': 'Nashville', 'r_state': 'TN', 'r_highSchool': 'Ensworth', 'r_position': 'DB', 'r_height': 72.0, 'r_weight': 180.0, 'r_stars': 4, 'r_nationalRank': 242.0, 'r_positionRank': 17.0, 'r_stateRank': 7.0, 'r_displayName': 'ricomcgraw', 'r_ID': 'ricomcgraw_georgia', 'r_IDYR': 'ricomcgraw_georgia_2015', 'school': 'georgia', 'year': '2015'}
{'r_rawSchool': 'Auburn', 'r_school': 'auburn', 'r_year': '2017', 'r_playerName': 'anderscarlson', 'r_city': '

{'r_rawSchool': 'Alabama', 'r_school': 'alabama', 'r_year': '2008', 'r_playerName': 'tylerlove', 'r_city': 'Mountain Brook', 'r_state': 'AL', 'r_highSchool': 'Mountain Brook', 'r_position': 'OL', 'r_height': 79.0, 'r_weight': 285.0, 'r_stars': 5, 'r_nationalRank': 30.0, 'r_positionRank': 8.0, 'r_stateRank': 3.0, 'r_displayName': 'tylerlove', 'r_ID': 'tylerlove_alabama', 'r_IDYR': 'tylerlove_alabama_2008', 'school': 'alabama', 'year': '2008'}
{'r_rawSchool': 'Mississippi', 'r_school': 'olemiss', 'r_year': '2004', 'r_playerName': 'davidtraxler', 'r_city': 'Jackson', 'r_state': 'MS', 'r_highSchool': 'Jackson Academy', 'r_position': 'OL', 'r_height': 78.0, 'r_weight': 260.0, 'r_stars': 2, 'r_nationalRank': nan, 'r_positionRank': nan, 'r_stateRank': nan, 'r_displayName': 'davidtraxler', 'r_ID': 'davidtraxler_olemiss', 'r_IDYR': 'davidtraxler_olemiss_2004', 'school': 'olemiss', 'year': '2004'}
{'r_rawSchool': 'Texas A&M', 'r_school': 'texasam', 'r_year': '2009', 'r_playerName': 'aaronarterbu

{'r_rawSchool': 'Alabama', 'r_school': 'alabama', 'r_year': '2015', 'r_playerName': 'mattwomack', 'r_city': 'Senatobia', 'r_state': 'MS', 'r_highSchool': 'Magnolia Heights', 'r_position': 'OL', 'r_height': 79.0, 'r_weight': 330.0, 'r_stars': 3, 'r_nationalRank': nan, 'r_positionRank': 67.0, 'r_stateRank': 17.0, 'r_displayName': 'mattwomack', 'r_ID': 'mattwomack_alabama', 'r_IDYR': 'mattwomack_alabama_2015', 'school': 'alabama', 'year': '2015'}
{'r_rawSchool': 'Auburn', 'r_school': 'auburn', 'r_year': '2016', 'r_playerName': 'princesammons', 'r_city': 'Cincinnati', 'r_state': 'OH', 'r_highSchool': 'Hills Christian Academy', 'r_position': 'DE', 'r_height': 78.0, 'r_weight': 260.0, 'r_stars': 4, 'r_nationalRank': nan, 'r_positionRank': 20.0, 'r_stateRank': 14.0, 'r_displayName': 'princesammons', 'r_ID': 'princesammons_auburn', 'r_IDYR': 'princesammons_auburn_2016', 'school': 'auburn', 'year': '2016'}
{'r_rawSchool': 'Florida', 'r_school': 'florida', 'r_year': '2011', 'r_playerName': 'chri

{'r_rawSchool': 'Arkansas', 'r_school': 'arkansas', 'r_year': '2017', 'r_playerName': 'kyreifisher', 'r_city': 'Tulsa', 'r_state': 'OK', 'r_highSchool': 'Union', 'r_position': 'LB', 'r_height': 74.0, 'r_weight': 227.0, 'r_stars': 3, 'r_nationalRank': nan, 'r_positionRank': 36.0, 'r_stateRank': 8.0, 'r_displayName': 'kyreifisher', 'r_ID': 'kyreifisher_arkansas', 'r_IDYR': 'kyreifisher_arkansas_2017', 'school': 'arkansas', 'year': '2017'}
{'r_rawSchool': 'South Carolina', 'r_school': 'southcarolina', 'r_year': '2007', 'r_playerName': 'dionlecorn', 'r_city': 'Ocala', 'r_state': 'FL', 'r_highSchool': 'Trinity Catholic', 'r_position': 'WR', 'r_height': 72.0, 'r_weight': 192.0, 'r_stars': 4, 'r_nationalRank': 122.0, 'r_positionRank': 17.0, 'r_stateRank': 19.0, 'r_displayName': 'dionlecorn', 'r_ID': 'dionlecorn_southcarolina', 'r_IDYR': 'dionlecorn_southcarolina_2007', 'school': 'southcarolina', 'year': '2007'}
{'r_rawSchool': 'Florida', 'r_school': 'florida', 'r_year': '2008', 'r_playerName'

KeyboardInterrupt: 

In [ ]:
df_finalSet = pandas.DataFrame(finalSet)
df_finalSet.head()